In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from matplotlib.animation import FFMpegWriter
from IPython.display import HTML

class BlackHole:
    def __init__(self, mass):
        self.mass = mass
        self.G = 6.6743e-11
        self.c = 2.998e8
        self.rs = 2 * self.G * self.mass / self.c**2

class Sun:
    def __init__(self, black_hole):
        self.mass = np.random.uniform(1e28, 1e30) / 10
        self.radius = np.random.uniform(4 * black_hole.rs, 6 * black_hole.rs)
        self.size = self.mass / 1e29 * 600
        self.angle = np.random.uniform(0, 2 * np.pi)
        self.black_hole = black_hole
        self.update_position()

    def gravitational_force(self):
        distance = max(self.radius, self.black_hole.rs)
        return self.black_hole.G * self.mass * self.black_hole.mass / (distance ** 2)

    def update_position(self):
        force = self.gravitational_force()
        orbit_speed = np.sqrt(force / self.mass)
        orbit_speed_mod = orbit_speed % self.black_hole.rs
        self.radius -= 0.05 * orbit_speed_mod
        self.angle += 0.05  
        self.x = self.radius * np.cos(self.angle)
        self.y = self.radius * np.sin(self.angle)
        self.z = -self.black_hole.rs**2 / (np.sqrt(self.x**2 + self.y**2) + self.black_hole.rs/10)


class SpaceTime:
    def __init__(self, black_hole, grid_size=100):
        self.black_hole = black_hole
        x = np.linspace(-6*black_hole.rs, 6*black_hole.rs, grid_size)
        y = np.linspace(-6*black_hole.rs, 6*black_hole.rs, grid_size)
        self.X, self.Y = np.meshgrid(x, y)
        self.Z = -black_hole.rs**2 / (np.sqrt(self.X**2 + self.Y**2) + black_hole.rs/10)

mass_bh = 1e30
black_hole = BlackHole(mass_bh)
space_time = SpaceTime(black_hole)
suns = []
max_suns = 10

def update(frame):
    ax.clear()
    ax.set_xlim([-6 * black_hole.rs, 6 * black_hole.rs])
    ax.set_ylim([-6 * black_hole.rs, 6 * black_hole.rs])
    ax.set_zlim([-2 * black_hole.rs, 2 * black_hole.rs])
    ax.view_init(elev=30, azim=30)
    ax.plot_wireframe(space_time.X, space_time.Y, space_time.Z, rstride=1, cstride=1, color='blue', alpha=0.2, zorder=0)

    if len(suns) < max_suns:
        suns.append(Sun(black_hole))

    for sun in suns:
        sun.update_position()
        if sun.radius > black_hole.rs * 1.1:
            ax.scatter(sun.x, sun.y, sun.z, color='darkorange', s=sun.size, alpha=1, zorder=1)
        elif sun.radius > black_hole.rs * 0.8:
            ax.scatter(sun.x, sun.y, sun.z, color='blue', s=sun.size, alpha=0.7, zorder=1)
        else:
            suns.remove(sun)
    return []

In [ ]:
print("Generating mp4, please wait...")
np.random.seed(0)
fig = plt.figure(figsize=(8, 6))
ax = plt.subplot2grid((1, 1), (0, 0), projection='3d')
ani = FuncAnimation(fig, 
                    update, 
                    frames=np.arange(750), 
                    interval=500, 
                    repeat=True, 
                    blit=True, 
                    repeat_delay=1000)
metadata = dict(title='Exploring the Event Horizon', artist='Aditya Rao',comment='Space Rocks!')
writer = FFMpegWriter(fps=25, bitrate=20000, metadata=metadata)
ani.save('animation.mp4', writer=writer, dpi=80)
print("File animation.mp4 generated!")

In [ ]:
HTML("""
    <video alt="Event Horizon Video" controls>
        <source src="animation.mp4" type="video/mp4">
    </video>
""")